In [1]:
import numpy as np 

import pandas as pd 
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json 

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim 

import requests
from pandas.io.json import json_normalize 

import matplotlib.cm as cm
import matplotlib.colors as colors


from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium 


Waiting for a Spark session to start...
Spark Initialization Done! ApplicationId = app-20181016040859-0000
Solving environment: done

## Package Plan ##

  environment location: /opt/ibm/conda/miniconda3

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    conda-4.5.11               |           py35_0         636 KB  conda-forge
    certifi-2018.8.24          |        py35_1001         139 KB  conda-forge
    ca-certificates-2018.8.24  |       ha4d7672_0         136 KB  conda-forge
    openssl-1.0.2p             |       h470a237_1         3.1 MB  conda-forge
    geopy-1.17.0               |             py_0          49 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         4.1 MB

The followin

In [4]:
!wget -q -O 'NY_data.json' https://ibm.box.com/shared/static/fbpwbovar7lf8p5sgddm06cgipa2rxpe.json
print("Data")

Data


In [6]:
with open('NY_data.json') as json_data:
    NY_data = json.load(json_data)

In [7]:
NY_data

{'bbox': [-74.2492599487305,
  40.5033187866211,
  -73.7061614990234,
  40.9105606079102],
 'crs': {'properties': {'name': 'urn:ogc:def:crs:EPSG::4326'}, 'type': 'name'},
 'features': [{'geometry': {'coordinates': [-73.84720052054902,
     40.89470517661],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.1',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661],
    'borough': 'Bronx',
    'name': 'Wakefield',
    'stacked': 1},
   'type': 'Feature'},
  {'geometry': {'coordinates': [-73.82993910812398, 40.87429419303012],
    'type': 'Point'},
   'geometry_name': 'geom',
   'id': 'nyu_2451_34572.2',
   'properties': {'annoangle': 0.0,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.874294193

In [10]:
n_data=NY_data['features']

In [12]:
n_data[0]

{'geometry': {'coordinates': [-73.84720052054902, 40.89470517661],
  'type': 'Point'},
 'geometry_name': 'geom',
 'id': 'nyu_2451_34572.1',
 'properties': {'annoangle': 0.0,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661],
  'borough': 'Bronx',
  'name': 'Wakefield',
  'stacked': 1},
 'type': 'Feature'}

In [14]:
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
Nhoods = pd.DataFrame(columns=column_names)
Nhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [21]:
for data in n_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    Nhoods = Nhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
Nhoods

Borough               Neighborhood   Latitude  Longitude
0             Bronx                  Wakefield  40.894705 -73.847201
1             Bronx                 Co-op City  40.874294 -73.829939
2             Bronx                Eastchester  40.887556 -73.827806
3             Bronx                  Fieldston  40.895437 -73.905643
4             Bronx                  Riverdale  40.890834 -73.912585
5             Bronx                Kingsbridge  40.881687 -73.902818
6         Manhattan                Marble Hill  40.876551 -73.910660
7             Bronx                   Woodlawn  40.898273 -73.867315
8             Bronx                    Norwood  40.877224 -73.879391
9             Bronx             Williamsbridge  40.881039 -73.857446
10            Bronx                 Baychester  40.866858 -73.835798
11            Bronx             Pelham Parkway  40.857413 -73.854756
12            Bronx                City Island  40.847247 -73.786488
13            Bronx               Bedford Park  40.870185 -73.885512
14            Bronx         University Heights  40.855727 -73.910416
15            Bronx             Morris Heights  40.847898 -73.919672
16            Bronx                    Fordham  40.860997 -73.896427
17            Bronx               East Tremont  40.842696 -73.887356
18            Bronx                 West Farms  40.839475 -73.877745
19            Bronx               High  Bridge  40.836623 -73.926102
20            Bronx                    Melrose  40.819754 -73.909422
21            Bronx                 Mott Haven  40.806239 -73.916100
22            Bronx                Port Morris  40.801664 -73.913221
23            Bronx                   Longwood  40.815099 -73.895788
24            Bronx                Hunts Point  40.809730 -73.883315
25            Bronx                 Morrisania  40.823592 -73.901506
26            Bronx                  Soundview  40.821012 -73.865746
27            Bronx               Clason Point  40.806551 -73.854144
28            Bronx                Throgs Neck  40.815109 -73.816350
29            Bronx               Country Club  40.844246 -73.824099
30            Bronx                Parkchester  40.837938 -73.856003
31            Bronx         Westchester Square  40.840619 -73.842194
32            Bronx                   Van Nest  40.843608 -73.866299
33            Bronx                Morris Park  40.847549 -73.850402
34            Bronx                    Belmont  40.857277 -73.888452
35            Bronx             Spuyten Duyvil  40.881395 -73.917190
36            Bronx            North Riverdale  40.908543 -73.904531
37            Bronx                 Pelham Bay  40.850641 -73.832074
38            Bronx              Schuylerville  40.826580 -73.826203
39            Bronx             Edgewater Park  40.821986 -73.813885
40            Bronx                Castle Hill  40.819014 -73.848027
41            Bronx                  Olinville  40.871371 -73.863324
42            Bronx             Pelham Gardens  40.862966 -73.841612
43            Bronx                  Concourse  40.834284 -73.915589
44            Bronx                  Unionport  40.829774 -73.850535
45            Bronx                   Edenwald  40.884561 -73.848083
46         Brooklyn                  Bay Ridge  40.625801 -74.030621
47         Brooklyn                Bensonhurst  40.611009 -73.995180
48         Brooklyn                Sunset Park  40.645103 -74.010316
49         Brooklyn                 Greenpoint  40.730201 -73.954241
50         Brooklyn                  Gravesend  40.595260 -73.973471
51         Brooklyn             Brighton Beach  40.576825 -73.965094
52         Brooklyn             Sheepshead Bay  40.586890 -73.943186
53         Brooklyn          Manhattan Terrace  40.614433 -73.957438
54         Brooklyn                   Flatbush  40.636326 -73.958401
55         Brooklyn              Crown Heights  40.670829 -73.943291
56         Brooklyn              East Flatbush  40.641718 -73.936103
57        

In [22]:
address = 'New York City, NY'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geo coordinate of New York City are {}, {}.'.format(latitude, longitude))


/opt/ibm/conda/miniconda3/lib/python3.5/site-packages/geopy/geocoders/osm.py:143: UserWarning: Using Nominatim with the default "geopy/1.17.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  UserWarning


The geo coordinate of New York City are 40.7308619, -73.9871558.


In [24]:
map_data = folium.Map(location=[latitude, longitude], zoom_start=10)


In [30]:
for lat, lng, borough, neighborhood in zip(Nhoods['Latitude'], Nhoods['Longitude'], Nhoods['Borough'], Nhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color="yellow",
        fill_opacity=0.9,
        parse_html=False).add_to(map_data)  
    
map_data

In [31]:
CLIENT_ID = 'LU1FRODZUVUD5IZKNLMYEN3Z10DZYJJX1PAHHGSNA5X5L5ZI' 
CLIENT_SECRET = 'T3OU4JPIYQCGTUSDCYVWGQPHRVRVWDZJIRH4PSL5X1WUPUE2' 
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: LU1FRODZUVUD5IZKNLMYEN3Z10DZYJJX1PAHHGSNA5X5L5ZI
CLIENT_SECRET:T3OU4JPIYQCGTUSDCYVWGQPHRVRVWDZJIRH4PSL5X1WUPUE2


In [35]:
search_query = 'Mexican,Italian'
radius = 1500
print(search_query + ' .... OK!')

Mexican,Italian .... OK!


In [36]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=LU1FRODZUVUD5IZKNLMYEN3Z10DZYJJX1PAHHGSNA5X5L5ZI&client_secret=T3OU4JPIYQCGTUSDCYVWGQPHRVRVWDZJIRH4PSL5X1WUPUE2&ll=40.7308619,-73.9871558&v=20180604&query=Mexican,Italian&radius=1500&limit=30'

In [37]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5bc5b699f594df1d9655a002'},
 'response': {'venues': [{'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/mexican_',
       'suffix': '.png'},
      'id': '4bf58dd8d48988d1c1941735',
      'name': 'Mexican Restaurant',
      'pluralName': 'Mexican Restaurants',
      'primary': True,
      'shortName': 'Mexican'}],
    'hasPerk': False,
    'id': '4b9ff08af964a5202a4c37e3',
    'location': {'address': '117 E 14th St',
     'cc': 'US',
     'city': 'New York',
     'country': 'United States',
     'distance': 395,
     'formattedAddress': ['117 E 14th St',
      'New York, NY 10003',
      'United States'],
     'lat': 40.7341525655372,
     'lng': -73.98891703333011,
     'postalCode': '10003',
     'state': 'NY'},
    'name': 'Chipotle Mexican Grill',
    'referralId': 'v-1539683993'},
   {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/mexican_',
       'suffix': '.png'},
      'id': '4bf

In [38]:
venues = results['response']['venues']

In [39]:
dataframe = json_normalize(venues)
dataframe.head()

categories delivery.id  \
0  [{'primary': True, 'icon': {'suffix': '.png', ...         NaN   
1  [{'primary': True, 'icon': {'suffix': '.png', ...         NaN   
2  [{'primary': True, 'icon': {'suffix': '.png', ...         NaN   
3  [{'primary': True, 'icon': {'suffix': '.png', ...         NaN   
4  [{'primary': True, 'icon': {'suffix': '.png', ...         NaN   

  delivery.provider.icon.name delivery.provider.icon.prefix  \
0                         NaN                           NaN   
1                         NaN                           NaN   
2                         NaN                           NaN   
3                         NaN                           NaN   
4                         NaN                           NaN   

  delivery.provider.icon.sizes delivery.provider.name delivery.url  hasPerk  \
0                          NaN                    NaN          NaN    False   
1                          NaN                    NaN          NaN    False   
2                          NaN                    NaN          NaN    False   
3                          NaN                    NaN          NaN    False   
4                          NaN                    NaN          NaN    False   

                         id            location.address location.cc  \
0  4b9ff08af964a5202a4c37e3               117 E 14th St          US   
1  4ec27c885c5c3d470deb0904                625 Broadway          US   
2  4a4925b7f964a52008ab1fe3               200 Varick St          US   
3  4ab3da04f964a520c36e20e3                 55 E 8th St          US   
4  4adf9c01f964a5200f7c21e3  405 Avenue of the Americas          US   

  location.city location.country                    location.crossStreet  \
0      New York    United States                                     NaN   
1      New York    United States              btwn Bleecker & Houston St   
2      New York    United States           Varick between Houston & King   
3      New York    United States  E 8th St between Broadway & University   
4      New York    United States                6th Ave and W 8th Street   

   location.distance                          location.formattedAddress  \
0                395  [117 E 14th St, New York, NY 10003, United Sta...   
1                953  [625 Broadway (btwn Bleecker & Houston St), Ne...   
2               1566  [200 Varick St (Varick between Houston & King)...   
3                535  [55 E 8th St (E 8th St between Broadway & Univ...   
4               1112  [405 Avenue of the Americas (6th Ave and W 8th...   

                             location.labeledLatLngs  location.lat  \
0                                                NaN     40.734153   
1  [{'label': 'display', 'lng': -73.9963947644429...     40.725929   
2  [{'label': 'display', 'lng': -74.0053756905017...     40.728128   
3  [{'label': 'display', 'lng': -73.9935033688602...     40.731060   
4  [{'label': 'display', 'lng': -73.9998457722392...     40.733596   

   location.lng location.postalCode location.state                    name  \
0    -73.988917               10003             NY  Chipotle Mexican Grill   
1    -73.996395               10012             NY  Chipotle Mexican Grill   
2    -74.005376               10014             NY  Chipotle Mexican Grill   
3    -73.993503               10003             NY  Chipotle Mexican Grill   
4    -73.999846               10014             NY  Chipotle Mexican Grill   

     referralId venuePage.id  
0  v-1539683993          NaN  
1  v-1539683993          NaN  
2  v-1539683993          NaN  
3  v-1539683993          NaN  
4  v-1539683993          NaN

In [40]:
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

In [41]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']
    
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
dataframe_filtered

name          categories  \
0                        Chipotle Mexican Grill  Mexican Restaurant   
1                        Chipotle Mexican Grill  Mexican Restaurant   
2                        Chipotle Mexican Grill  Mexican Restaurant   
3                        Chipotle Mexican Grill  Mexican Restaurant   
4                        Chipotle Mexican Grill  Mexican Restaurant   
5                 Tableside Italian Cook Shoppe  Italian Restaurant   
6                        Chipotle Mexican Grill  Mexican Restaurant   
7    Modern Kitchen Design Cabinets | Cesar NYC    Business Service   
8                 Zaragoza Mexican Deli-Grocery  Mexican Restaurant   
9                  Lusterini Italian Restaurant  Italian Restaurant   
10                 Faicco's Italian Specialties      Sandwich Place   
11                        Mexican General Store          Taco Place   
12                      Italian American Museum      History Museum   
13                          Mexican Street Cart  Mexican Restaurant   
14                       Italian Sparkle Palace  Italian Restaurant   
15                            Mexican Foodtruck          Food Truck   
16                       Chipotle Mexican Grill  Mexican Restaurant   
17                Al Horno Lean Mexican Kitchen  Mexican Restaurant   
18                       Italian Wine Merchants           Wine Shop   
19                   La Sirena Mexican Folk Art           Gift Shop   
20                           Mexican Food Truck          Food Truck   
21                         Mexican Radio Dinner  Mexican Restaurant   
22                       Chipotle Mexican Grill  Mexican Restaurant   
23                 Tri Mexican Tacos Food Truck          Food Truck   
24  Johnny Mozzarella's Italian Eatery and Cafe                Food   
25                  La Bella Italian Restaurant  Italian Restaurant   
26                           Olive Tree Italian  Italian Restaurant   
27                       Chipotle Mexican Grill  Mexican Restaurant   
28                                  Dos Caminos  Mexican Restaurant   
29                                Johns Italian  Italian Restaurant   

                       address  cc      city        country  \
0                117 E 14th St  US  New York  United States   
1                 625 Broadway  US  New York  United States   
2                200 Varick St  US  New York  United States   
3                  55 E 8th St  US  New York  United States   
4   405 Avenue of the Americas  US  New York  United States   
5                 345 E 6th St  US  New York  United States   
6                 864 Broadway  US  New York  United States   
7                 50 W 23rd St  US  New York  United States   
8                 215 Avenue A  US  New York  United States   
9                    Hester St  US  New York  United States   
10             260 Bleecker St  US  New York  United States   
11                 63 E 4th St  US  New York  United States   
12             155 Mulberry St  US  New York  United States   
13          Ave A and E 2nd St  US  New York  United States   
14                 13th Street  US  New York  United States   
15                         NaN  US  New York  United States   
16                71 Spring St  US  New York  United States   
17                  57 1st Ave  US  New York  United States   
18               108 E 16th St  US  New York  United States   
19                 27 E 3rd St  US  New York  United States   
20                 23rd Street  US  New York  United States   
21                         NaN  US  New York  United States   
22               125 E 23rd St  US  New York  United States   
23                901 Broadway  US  New York  United States   
24               328 E 14th St  US  New York  United States   
25               349 E 12th St  US  New York  United States   
26           182 Lexington Ave  US  New York  United States   
27                 286 1st Ave  US  New York  United States   
28            

In [51]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) 


folium.features.CircleMarker(
    [latitude, longitude],
    radius=10,
    color='red',
    popup='Conrad Hotel',
    fill = True,
    fill_color = 'red',
    fill_opacity = 0.6
).add_to(venues_map)

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

In [50]:
limit=20
user_id = '484542633'
url = 'https://api.foursquare.com/v2/users/{}/tips?client_id={}&client_secret={}&v={}&limit={}'.format(user_id, CLIENT_ID, CLIENT_SECRET, VERSION, limit)


results = requests.get(url).json()
tips = results['response']['tips']['items']


pd.set_option('display.max_colwidth', -1)

tips_df = json_normalize(tips)


filtered_columns = ['text', 'agreeCount', 'disagreeCount', 'id']
tips_filtered = tips_df.loc[:, filtered_columns]


tips_filtered

text  \
0   The best! I’m especially fond of the salmon burger, but I’ve had half of the menu and never been disappointed. There’s a reason this place is well known even outside of the Village!             
1   I used to down a pint of chocolate like it was nothing back when I was bulking. Highly recommended!                                                                                               
2   They serve coffee!!!!!!                                                                                                                                                                           
3   I’m a fan. In fact, I’m such a big fan, I want Taim to hire me to be their spokesman. Kind of like the Arabic Jared Fogle - but without the kid stuff.                                            
4   The linguine with clams is on point 👌                                                                                                                                                             
5   Great for a quick, cheap lunch! Shorter lines than Chipotle too👌                                                                                                                                  
6   Quick, cheap lunch that tastes good! Way shorter line than Chipotle, too.                                                                                                                         
7   Great for a quick, cheap bite. I stop by when I’m in the neighborhood and don’t have much time to eat.                                                                                            
8   You’re not a real New Yorker until you’ve shame-ordered Insomnia Cookies for delivery at 3am                                                                                                      
9   Good for you yet still tasty! Clean green protein is my go-to after I hit the gym 💪                                                                                                               
10  Coffee game on point                                                                                                                                                                              
11  This is the dive bar to end all other dive bars. Go here if you like cheap drinks! 🥃                                                                                                              
12  Burger game strong 💪                                                                                                                                                                              
13  Great burgers & fries! Also, this place is exactly what it’s like when you go to a bar in the Southwest. Source: I’m from Arizona.                                                                
14  That guy looks familiar...                                                                                                                                                                        
15  Açaí bowl + peanut butter + whey protein = 💪💪💪                                                                                                                                                    
16  Highly underrated and way less crowded than Central Park!                                                                                                                                         
17  Way easier to navigate than the Met proper, plus the Met Breuer focuses on modern art. If I only have a limited amount of time to spend in a museum, I would rather go here than anywhere else!   
18  Get the açaí bowl with peanut butter after your work out and thank me later 👌                                                                                                                     
19  When you want a burger, this should be the first thing that comes to mind. A+!                                                                                                                    

    agreeCo